# 0. Import Libraries

In [1]:
import pandas as pd
import numpy as np
import cv2 as cv
import matplotlib.pyplot as plt
import os

# 1. Volume and Perimeter calculation in 2D space

In [2]:
d = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/coating_ncm_id.csv')
id_list = d['id'].tolist()

In [3]:
def volumeperi(d):
    file = d['file'].tolist()[0]
    df = pd.read_csv(file).drop(['Unnamed: 0', 'center'], axis = 1)

    area_tot = []
    length_tot = []
    col_list = df.columns.tolist()
    frame_list = df['#frame'].tolist()
    center_tot = []
    dist_tot = []
    
    three_center = []
    for col in col_list[1:]:
        ncm_list = df[col].tolist()
        area_list = []
        length_list = []
        center_list = []
        dist_list = []
        pore_center_list = []
        
        cen_list_3d = []
        for i in range(len(frame_list)):
            if  np.isnan(ncm_list[i]) != True:
                target_frame = int(frame_list[i])
                target_ncm = int(ncm_list[i])
                d_target = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/1.coating/ncm_pore_id_cordi/frame' + str(target_frame) + '.csv')

                ncm = np.array(eval( d_target['ncm_cordi'].tolist()[target_ncm]))
                pore = eval( d_target['pore'].tolist()[target_ncm])

                M = cv.moments(ncm)
                
                cx = int(M['m10']/M['m00'])
                cy = int(M['m01']/M['m00'])
                ncm_center = np.array([cx, cy])
                base = np.array([600,840])
                dist = np.linalg.norm(ncm_center-base)
                
                center_3d = [cx, cy]
                
                cen_list_3d.append([cx, cy, target_frame])
                ncm_area = M['m00'] # sum == volume 
                ncm_length = cv.arcLength(ncm, False) # sum == surface area

                area_list.append(ncm_area)
                length_list.append(ncm_length)
                center_list.append(center_3d)
                
                dist_list.append(dist)
                
        area_tot.append(area_list)
        length_tot.append(length_list)
        center_tot.append(center_list)
        three_center.append(cen_list_3d)
        dist_tot.append(dist_list)

    return area_tot, length_tot, d_target, center_tot, dist_tot, three_center

In [57]:
volume, peri = [], []
center = []
dist = []
dist_mean = []
frame_per_uni = []
frame_per_uni_sum = []
id_per_center = []

for i in id_list:
    d = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/bare_ncm_id.csv')
    data = d[d['id'] == i]
    area_tot, length_tot, d_target, center_tot, dist_tot, three_center = volumeperi(data)

    v_l = [np.sum(area) for area in area_tot]
    p_l = [np.sum(length) for length in length_tot]
    d_l = [np.mean(di) for di in dist_tot]


    uni_l = []
    for t in range(len(area_tot)):
        ul = [length_tot[t][k]/area_tot[t][k] for k in range(len(area_tot[t]))]
        uni_l.append(ul)

    un_l = [np.sum(u) for u in uni_l]
    volume.append(v_l)
    peri.append(p_l) 
    dist_mean.append(d_l)
    dist.append(dist_tot)
    frame_per_uni.append(uni_l)
    frame_per_uni_sum.append(un_l)

    th_l = []
    for th in range(len(three_center)):
        th_l = th_l + three_center[th]
    x_cen = np.array(th_l)[:,0]
    y_cen = np.array(th_l)[:,1]
    z_cen = np.array(th_l)[:,2]
    id_per_center.append([np.mean(x_cen), np.mean(y_cen), np.mean(z_cen)])


In [2]:
feature_b = pd.DataFrame({})
feature_b['ncm_ind'] = id_list
feature_b['volume_raw'] = volume
feature_b['volume'] = [np.sum(v) for v in volume]
feature_b['surface_area_raw'] = peri
feature_b['surface_area'] = [np.sum(l) for l in peri]
feature_b['dist_from_center'] = dist
feature_b['dist_mean'] = dist_mean
feature_b['frame_per_uniformity_raw'] = frame_per_uni_sum
feature_b['frame_per_uniformity'] = [np.sum(i) for i in frame_per_uni_sum]

# 2. Contact area calculation in 2D space

In [59]:
def contact(d):
    file = d['file'].tolist()[0]
    df = pd.read_csv(file).drop(['Unnamed: 0', 'center'], axis = 1)

    adc_p_tot, adc_ncm_tot, adc_p_1_tot, adc_ncm_1_tot = [], [], [], []
    adc_p_sur_tot, adc_p_vol_tot = [], []
    
    col_list = df.columns.tolist()
    frame_list = df['#frame'].tolist()
    for col in col_list[1:]:
        ncm_list = df[col].tolist()
        adc_p_l, adc_ncm_l, adc_p_1_l, adc_ncm_1_l, adc_p_sur_l, adc_p_vol_l = [], [], [], [], [], []

        for i in range(len(frame_list)):
            if  np.isnan(ncm_list[i]) != True:
                target_frame = int(frame_list[i])
                target_ncm = int(ncm_list[i])
                d_target = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/0.bare/ncm_pore_id_cordi/frame' + str(target_frame) + '.csv')
                ncm = np.array(eval( d_target['ncm_cordi'].tolist()[target_ncm]))
                pore = eval( d_target['pore'].tolist()[target_ncm])
                
                adc_pore = []
                adc_ncm = []
                adc_pore_1 = []
                adc_ncm_1 = []
                
                p = []
                for cout in range(len(pore)):
                    p = p + pore[cout]
                    
                p1 = []
                for cout in range(len(p)):
                    p1 = p1 + p[cout]
                p2 = np.array(p1)
                
                for p3 in p2:                    
                    filt = []
                    for n in ncm:
                        dist = np.linalg.norm(n-p3)
                        filt.append(dist)                    
                    if filt.count(1.0) >= 1: 
                        adc_pore = adc_pore + [p3.tolist()]

                for p3 in p2:
                    filt = []
                    for n in ncm:
                        dist = np.linalg.norm(n-p3)
                        filt.append(dist)                        
                    count_l = 0
                    for f in filt:
                        if 1.0 <= f <= 2.0 : 
                            count_l = count_l + 1                            
                    if count_l >= 1:
                        adc_pore_1 = adc_pore_1 + [p3.tolist()]
                        
                for n in ncm:
                    filt = []
                    for p3 in p2:
                        dist = np.linalg.norm(n-p3)
                        filt.append(dist)     
                    if filt.count(1.0) >= 1:
                        adc_ncm = adc_ncm + n.tolist()
                        
                for n in ncm:
                    filt = []
                    for p3 in p2:
                        dist = np.linalg.norm(n-p3)
                        filt.append(dist)
                        
                    if filt != []:
                        print(np.min(filt))
                        
                    count_l = 0
                    for f in filt:
                        if 1.0 <= f  <= 2.0 : 
                            count_l = count_l + 1
                    if count_l >= 1:
                        adc_ncm_1 = adc_ncm_1 + n.tolist()
                
                adc_p_l.append(adc_pore)
                adc_ncm_l.append(adc_ncm)
                adc_p_1_l.append(adc_pore_1)
                adc_ncm_1_l.append(adc_ncm_1)
              
        adc_p_tot.append(adc_p_l)
        adc_ncm_tot.append(adc_ncm_l)
        adc_p_1_tot.append(adc_p_1_l)
        adc_ncm_1_tot.append(adc_ncm_1_l)
        
    return adc_p_tot, adc_ncm_tot, adc_p_1_tot, adc_ncm_1_tot

# 3. Feature calculation in 3D space

In [60]:
contacted_area, c_1_pore, c_1_ncm = [], [], [] 
contacted_mean, adc_area_l, adc_area_l_ncm  = [], [], []
contacted_area_ncm, contacted_mean_ncm, check_list = [],[],[]

for i in id_list:
    d = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/bare_ncm_id.csv')
    data = d[d['id'] == i]
    adc_p_tot, adc_ncm_tot, adc_p_1_tot, adc_ncm_1_tot = contact(data)
    check_list.append(adc_ncm_tot)

## pore_face    
    adc_area = []
    for adc in adc_p_tot: 
        for ad in adc:
            if len(ad)!=0:
                ad0 = np.array(ad)
                ad0 = cv.arcLength(ad0, False)
                adc_area.append(ad0)
    adc_area_l.append(adc_area)
                
    if adc_area != []:
        contacted_area.append(sum(adc_area))
        contacted_mean.append(np.mean(adc_area))
    elif adc_area == []:
        contacted_area.append(0)
        contacted_mean.append(0)
        
## ncm_face
    adc_area = []
    for adc in adc_ncm_tot: 
        for ad in adc:
            if len(ad)!=0:
                ad0 = np.array(ad)
                ad0 = cv.arcLength(ad0, False)
                adc_area.append(ad0)
    adc_area_l_ncm.append(adc_area)
                
    if adc_area != []:
        contacted_area_ncm.append(sum(adc_area))
        contacted_mean_ncm.append(np.mean(adc_area))
    elif adc_area == []:
        contacted_area_ncm.append(0)
        contacted_mean_ncm.append(0)       
        
    adc_1_p_area = []
    for adc in adc_p_1_tot: 
        for ad in adc:
            if len(ad)!=0:
                ad0 = np.array(ad)
                ad0 = cv.arcLength(ad0, False)
                adc_1_p_area.append(ad0)
              
    if adc_1_p_area != []:
        c_1_pore.append(sum(adc_1_p_area))
    elif adc_1_p_area == []:
        c_1_pore.append(0)
  
    adc_1_ncm_area = []
    for adc in adc_ncm_1_tot: 
        for ad in adc:
            if len(ad)!=0:
                ad0 = np.array(ad)
                ad0 = cv.arcLength(ad0, False)
                adc_1_ncm_area.append(ad0)
              
    if adc_1_ncm_area != []:
        c_1_ncm.append(sum(adc_1_ncm_area))
    elif adc_1_ncm_area == []:
        c_1_ncm.append(0)

14.317821063276353
13.92838827718412
14.560219778561036
15.524174696260024
16.15549442140351
17.08800749063506
18.027756377319946
18.973665961010276
19.6468827043885
20.615528128088304
21.587033144922902
21.095023109728988
21.470910553583888
21.93171219946131
21.540659228538015
22.135943621178654
21.840329667841555
21.587033144922902
22.360679774997898
22.20360331117452
23.08679276123039
24.020824298928627
25.019992006393608
26.019223662515376
26.0
26.0
27.0
27.018512172212592
26.076809620810597
25.179356624028344
25.317977802344327
25.495097567963924
24.73863375370596
25.0
24.041630560342615
22.80350850198276
21.840329667841555
21.18962010041709
20.248456731316587
19.313207915827967
18.384776310850235
17.46424919657298
16.55294535724685
16.1245154965971
15.231546211727817
14.7648230602334
14.422205101855956
13.601470508735444
13.45362404707371
12.727922061357855
11.313708498984761
9.899494936611665
9.219544457292887
8.48528137423857
7.810249675906654
7.211102550927978
5.83095189484530

1.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
1.0
1.0
2.23606797749979
3.605551275463989
5.0
6.0
7.0
8.0
9.0
10.0
11.045361017187261
12.041594578792296
13.038404810405298
14.035668847618199
15.033296378372908
16.0312195418814
17.029386365926403
17.72004514666935
18.681541692269406
19.6468827043885
20.396078054371138
21.213203435596427
22.20360331117452
23.194827009486403
24.08318915758459
25.019992006393608
24.0
24.020824298928627
24.08318915758459
24.186773244895647
24.331050121192877
24.515301344262525
25.709920264364882
26.92582403567252
26.248809496813376
27.51363298439521
27.85677655436824
28.231188426986208
28.635642126552707
29.068883707497267
29.5296461204668
30.886890422961002
31.32091952673165
31.575306807693888
31.400636936215164
31.25699921617557
30.14962686336267
30.066592756745816
30.01666203960727
30.0
29.017236257093817
28.071337695236398
28.160255680657446
27.294688127912362
26.476404589747453
25.709920264364882
25.0
24.041630560342615
2

2.0
1.0
1.0
1.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.8284271247461903
2.8284271247461903
2.23606797749979
1.0
1.0
2.0
3.1622776601683795
4.123105625617661
5.385164807134504
6.708203932499369
8.06225774829855
8.602325267042627
10.0
10.63014581273465
11.313708498984761
12.727922061357855
12.206555615733702
11.40175425099138
10.0
9.219544457292887
7.810249675906654
6.4031242374328485
5.0
4.47213595499958
3.1622776601683795
2.23606797749979
1.0
1.0
2.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
3.0
4.0
5.0
6.0
5.830951894845301
4.47213595499958
3.605551275463989
2.8284271247461903
2.23606797749979
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
2.23606797749979
3.1622776601683795
4.47213595499958
5.385164807134504
6.324555320336759
7.615773105863909
8.54400374531753
9.8488578017961

31.064449134018133
31.38470965295043
31.76476034853718
32.202484376209235
33.1058907144937
33.61547262794322
34.17601498127012
35.11409973215888
35.73513677041127
36.40054944640259
37.107950630558946
38.07886552931954
38.47076812334269
38.91015291668744
39.81205847478876
40.311288741492746
40.85339643163099
41.43669871020132
42.37924020083418
43.01162633521314
42.720018726587654
43.41658669218482
43.174066289845804
42.95346318982906
42.7551166528639
42.579337712087536
41.43669871020132
41.30375285612676
40.19950248448356
40.11234224026316
40.049968789001575
40.01249804748511
40.0
39.0
38.0
37.0
36.013886210738214
35.05709628591621
34.058772731852805
33.06055050963308
32.14031735997639
31.144823004794873
30.14962686336267
29.154759474226502
28.071337695236398
27.073972741361768
26.076809620810597
25.179356624028344
24.186773244895647
23.194827009486403
22.20360331117452
21.213203435596427
20.223748416156685
19.4164878389476
18.24828759089466
17.26267650163207
16.492422502470642
15.81138

1.4142135623730951
2.0
2.23606797749979
3.605551275463989
4.242640687119285
5.0
5.830951894845301
6.4031242374328485
7.810249675906654
8.48528137423857
9.899494936611665
10.63014581273465
11.313708498984761
12.727922061357855
13.45362404707371
14.212670403551895
14.866068747318506
15.556349186104045
16.278820596099706
17.029386365926403
17.204650534085253
18.027756377319946
18.867962264113206
19.72308292331602
20.12461179749811
18.788294228055936
19.1049731745428
18.439088914585774
17.804493814764857
17.204650534085253
16.64331697709324
16.1245154965971
16.55294535724685
16.15549442140351
16.76305461424021
15.524174696260024
15.297058540778355
15.132745950421556
15.033296378372908
15.0
14.035668847618199
13.152946437965905
12.165525060596439
11.180339887498949
10.198039027185569
9.219544457292887
8.06225774829855
7.0710678118654755
6.082762530298219
5.0990195135927845
4.123105625617661
3.1622776601683795
2.23606797749979
1.4142135623730951
1.0
1.0
1.0
2.0
2.0
2.0
2.0
3.0
2.0
1.41421356

...

1.4142135623730951
2.23606797749979
3.605551275463989
4.242640687119285
5.0
4.242640687119285
2.8284271247461903
2.23606797749979
2.8284271247461903
3.605551275463989
4.242640687119285
5.656854249492381
6.708203932499369
7.615773105863909
8.54400374531753
9.433981132056603
9.848857801796104
8.54400374531753
7.615773105863909
6.324555320336759
7.280109889280518
8.246211251235321
9.219544457292887
9.486832980505138
10.770329614269007
12.083045973594572
12.649110640673518
13.152946437965905
12.041594578792296
11.180339887498949
10.198039027185569
9.486832980505138
9.848857801796104
11.180339887498949
11.661903789690601
12.206555615733702
12.041594578792296
11.313708498984761
9.899494936611665
8.48528137423857
7.810249675906654
7.211102550927978
7.615773105863909
6.324555320336759
5.385164807134504
4.47213595499958
3.1622776601683795
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
1.0
1.4142135623730951
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
3.1622776601683795
3.605551275463

1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
3.0
4.0
5.0
6.0
6.4031242374328485
7.0710678118654755
7.810249675906654
8.602325267042627
9.433981132056603
9.848857801796104
10.44030650891055
11.180339887498949
11.045361017187261
12.041594578792296
13.0
14.0
15.033296378372908
16.1245154965971
16.278820596099706
16.492422502470642
16.76305461424021
18.027756377319946
18.384776310850235
19.313207915827967
20.615528128088304
21.540659228538015
22.47220505424423
23.769728648009426
24.698178070456937
26.0
26.92582403567252
28.231188426986208
29.154759474226502
30.083217912982647
31.016124838541646
31.953090617340916
31.622776601683793
32.28002478313795
32.984845004941285
33.734255586866
34.52535300326414
35.35533905932738
36.345563690772494
37.21558813185679
37.12142238654117
38.05259518088089
39.05124837953327
40.049968789001575
41.048751503547585
42.04759208325728
43.04648650006177
44.01136216933077
45.0111097397076
46.010868281309364
47.0
47.01063709417264
47.042533945356304
46.097722286464

2.0
3.1622776601683795
3.605551275463989
5.0
6.4031242374328485
7.810249675906654
8.48528137423857
9.219544457292887
8.48528137423857
8.602325267042627
10.0
10.63014581273465
12.041594578792296
12.727922061357855
14.142135623730951
14.866068747318506
16.278820596099706
16.97056274847714
18.384776310850235
19.79898987322333
20.518284528683193
21.18962010041709
22.47220505424423
22.847319317591726
22.360679774997898
22.825424421026653
23.323807579381203
24.698178070456937
25.238858928247925
26.627053911388696
28.0178514522438
29.410882339705484
30.23243291566195
30.528675044947494
31.38470965295043
32.7566787083184
33.28663395418648
34.66987164671943
35.22782990761707
36.61966684720111
37.20215047547655
37.8021163428716
39.20459156782532
39.824615503479755
41.23105625617661
41.86884283091664
42.5205832509386
43.93176527297759
44.598206241955516
45.27692569068709
45.967379738244816
46.66904755831214
47.38143096192854
48.104053883222775
48.83646178829912
48.16637831516918
48.27007354458868

26.0
25.495097567963924
24.596747752497688
24.041630560342615
23.08679276123039
22.20360331117452
21.213203435596427
20.223748416156685
19.1049731745428
18.027756377319946
16.76305461424021
15.811388300841896
14.560219778561036
13.601470508735444
12.649110640673518
11.704699910719626
10.770329614269007
9.848857801796104
8.94427190999916
8.0
6.708203932499369
5.830951894845301
4.47213595499958
3.605551275463989
2.8284271247461903
2.0
1.4142135623730951
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.4142135623730951
2.23606797749979
3.605551275463989
4.47213595499958
5.830951894845301
7.211102550927978
8.602325267042627
10.0
10.63014581273465
11.313708498984761
11.313708498984761
11.180339887498949
12.529964086141668
13.416407864998739
14.7648230602334
15.556349186104045
16.97056274847714
18.35755975068582
18.027756377319946
17.804493814764857
17.69180601295413
17.69180601295413
18.439088914585774
19.1049731745428
19.4164878389476
18.439088914585774
17.46424919657298
16.492422502470642
15.297058540778355

1.0
2.0
3.0
4.0
5.0
6.0
7.0
8.0
9.0
10.0
11.0
12.0
12.0
12.041594578792296
10.816653826391969
10.0
8.602325267042627
7.810249675906654
7.0710678118654755
5.656854249492381
5.0
4.242640687119285
3.605551275463989
3.1622776601683795
2.8284271247461903
1.4142135623730951
1.0
2.0
2.0
2.23606797749979
2.0
2.0
3.1622776601683795
2.8284271247461903
2.23606797749979
1.0
1.4142135623730951
1.0
1.4142135623730951
2.0
2.8284271247461903
2.0
1.0
1.0
1.4142135623730951
2.8284271247461903
3.0
3.1622776601683795
2.0
2.0
1.4142135623730951
1.4142135623730951
2.0
2.0
3.0
4.0
5.0
6.0
7.0
8.0
9.0
10.0
11.0
12.0
12.206555615733702
11.40175425099138
10.0
9.219544457292887
7.810249675906654
7.0710678118654755
6.4031242374328485
5.830951894845301
4.47213595499958
3.605551275463989
2.8284271247461903
2.23606797749979
1.0
1.4142135623730951
1.4142135623730951
1.0
2.0
2.23606797749979
1.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
1.4142135623730951
1.0
1.4142135623730951
1.0
1.0
1.4142135623730951
2.0
2.0
3.0
2.0
2.236067977

In [61]:
feature_b['contact_area_pore_side'] = contacted_area
feature_b['contact_area_mean_pore_side'] = contacted_mean
feature_b['contact_area_ncm_side'] = contacted_area_ncm
feature_b['contact_area_mean_ncm_side'] = contacted_mean_ncm
feature_b['contact_area_extended_pore'] = c_1_pore
feature_b['contact_area_extended_ncm'] = c_1_ncm
feature_b


ncm_ind         volume_raw   volume  \
0          0           [2304.5]   2304.5   
1          1          [13894.5]  13894.5   
2          2           [1068.0]   1068.0   
3          3           [3837.5]   3837.5   
4          4          [26733.5]  26733.5   
..       ...                ...      ...   
495      495            [882.5]    882.5   
496      496            [509.5]    509.5   
497      497           [7214.5]   7214.5   
498      498  [54172.0, 4325.0]  58497.0   
499      499           [3760.5]   3760.5   

                           surface_area_raw  surface_area  \
0                        [751.369619011879]    751.369619   
1                       [2526.353585600853]   2526.353586   
2                      [400.66399443149567]    400.663994   
3                      [1088.6559777259827]   1088.655978   
4                       [4019.016703605652]   4019.016704   
..                                      ...           ...   
495                    [456.50461411476135]    456.504614   
496                    [221.09545290470123]    221.095453   
497                     [1850.184977054596]   1850.184977   
498  [7673.57042324543, 1191.4894571304321]   8865.059880   
499                    [1161.6193999052048]   1161.619400   

                                      dist_from_center  \
0    [[241.00622398602076, 241.00622398602076, 241....   
1    [[203.00246303924493, 203.00246303924493, 203....   
2    [[372.7800960351826, 373.99064159414473, 373.0...   
3    [[946.1469230515945, 944.7645209257172, 943.92...   
4    [[524.4091913763526, 523.442451469118, 522.220...   
..                                                 ...   
495  [[377.0331550407736, 376.14491888100787, 376.3...   
496  [[591.8487982584742, 591.8487982584742, 590.71...   
497  [[846.1784681732336, 844.7674236143342, 844.10...   
498  [[812.8726837580409, 812.8726837580409, 811.93...   
499  [[351.6546601425893, 350.4868043165106, 351.30...   

                                  dist_mean  \
0                       [240.9248646308442]   
1                      [201.81956560596493]   
2                      [372.14773869274313]   
3                       [942.8262352497466]   
4                       [525.0500333105152]   
..                                      ...   
495                     [376.0547642870997]   
496                     [591.0496404703846]   
497                     [841.8342718240234]   
498  [792.7685975331291, 762.1675783140787]   
499                    [351.59691060176044]   

                   frame_per_uniformity_raw  frame_per_uniformity  \
0                         [5.3457560570145]              5.345756   
1                       [6.782632269067978]              6.782632   
2                       [3.796750456930338]              3.796750   
3                       [6.142013587361969]              6.142014   
4                       [6.848908550979194]              6.848909   
..                                      ...                   ...   
495                     [6.733815305525624]              6.733815   
496                     [2.603635188420545]              2.603635   
497                    [7.8258723469278415]              7.825872   
498  [9.145341336603172, 6.027171525416321]             15.172513   
499                     [7.852636209787166]              7.852636   

     contact_area_pore_side  contact_area_mean_pore_side  \
0                  0.000000                     0.000000   
1                466.622762                    27.448398   
2                  9.000000                     9.000000   
3                  6.472136                     2.157379   
4                 71.398977                    11.899829   
..                      ...                          ...   
495                0.000000                     0.000000   
496                0.000000                     0.000000   
497               54.308159                     6.788520   
498              426.717919                    17.06

In [62]:
feature_b.to_csv('/home/sbml/Desktop/0.solid_electrolyte/feature_extraction_240728/extracted_bare.csv')

# 4. Number of adjacent pores 

In [63]:
d_bare = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/0.bare/pore_listup_240722.csv')
pore_cate = d_bare['pore_category'].tolist()
pore_cate = [eval(i) for i in pore_cate]
l = []
for i in pore_cate:
    l.append(len(set(i)))

In [64]:
feature_b['concated_pore_number'] = l
feature_b

ncm_ind         volume_raw   volume  \
0          0           [2304.5]   2304.5   
1          1          [13894.5]  13894.5   
2          2           [1068.0]   1068.0   
3          3           [3837.5]   3837.5   
4          4          [26733.5]  26733.5   
..       ...                ...      ...   
495      495            [882.5]    882.5   
496      496            [509.5]    509.5   
497      497           [7214.5]   7214.5   
498      498  [54172.0, 4325.0]  58497.0   
499      499           [3760.5]   3760.5   

                           surface_area_raw  surface_area  \
0                        [751.369619011879]    751.369619   
1                       [2526.353585600853]   2526.353586   
2                      [400.66399443149567]    400.663994   
3                      [1088.6559777259827]   1088.655978   
4                       [4019.016703605652]   4019.016704   
..                                      ...           ...   
495                    [456.50461411476135]    456.504614   
496                    [221.09545290470123]    221.095453   
497                     [1850.184977054596]   1850.184977   
498  [7673.57042324543, 1191.4894571304321]   8865.059880   
499                    [1161.6193999052048]   1161.619400   

                                      dist_from_center  \
0    [[241.00622398602076, 241.00622398602076, 241....   
1    [[203.00246303924493, 203.00246303924493, 203....   
2    [[372.7800960351826, 373.99064159414473, 373.0...   
3    [[946.1469230515945, 944.7645209257172, 943.92...   
4    [[524.4091913763526, 523.442451469118, 522.220...   
..                                                 ...   
495  [[377.0331550407736, 376.14491888100787, 376.3...   
496  [[591.8487982584742, 591.8487982584742, 590.71...   
497  [[846.1784681732336, 844.7674236143342, 844.10...   
498  [[812.8726837580409, 812.8726837580409, 811.93...   
499  [[351.6546601425893, 350.4868043165106, 351.30...   

                                  dist_mean  \
0                       [240.9248646308442]   
1                      [201.81956560596493]   
2                      [372.14773869274313]   
3                       [942.8262352497466]   
4                       [525.0500333105152]   
..                                      ...   
495                     [376.0547642870997]   
496                     [591.0496404703846]   
497                     [841.8342718240234]   
498  [792.7685975331291, 762.1675783140787]   
499                    [351.59691060176044]   

                   frame_per_uniformity_raw  frame_per_uniformity  \
0                         [5.3457560570145]              5.345756   
1                       [6.782632269067978]              6.782632   
2                       [3.796750456930338]              3.796750   
3                       [6.142013587361969]              6.142014   
4                       [6.848908550979194]              6.848909   
..                                      ...                   ...   
495                     [6.733815305525624]              6.733815   
496                     [2.603635188420545]              2.603635   
497                    [7.8258723469278415]              7.825872   
498  [9.145341336603172, 6.027171525416321]             15.172513   
499                     [7.852636209787166]              7.852636   

     contact_area_pore_side  contact_area_mean_pore_side  \
0                  0.000000                     0.000000   
1                466.622762                    27.448398   
2                  9.000000                     9.000000   
3                  6.472136                     2.157379   
4                 71.398977                    11.899829   
..                      ...                          ...   
495                0.000000                     0.000000   
496                0.000000                     0.000000   
497               54.308159                     6.788520   
498              426.717919                    17.06

In [65]:
feature_b.to_csv('/home/sbml/Desktop/0.solid_electrolyte/feature_extraction_240728/extracted_bare.csv')

# 5. Silhoutte coefficient in 3D space

In [3]:
from sklearn import metrics
from sklearn.cluster import KMeans
d_bare = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/id_240728/0.bare/pore_listup_240722.csv')
ncm_ind = d_bare['ncm_id'].tolist()
sil_list, sil_k_list = [], []
cal_list, cal_k_list = [], []

for i in ncm_ind:
    d = d_bare[d_bare['ncm_id'] == i]
    x = eval(d['cen_x'].tolist()[0])
    y = eval(d['cen_y'].tolist()[0])
    z = eval(d['frame_list'].tolist()[0])
    c_list = np.array(eval(d['pore_category'].tolist()[0]))
    
    
    data = pd.DataFrame({})
    data['x'] = x
    data['y'] = y
    data['z'] = z
    
    if len(data) == 0: 
        sil_list.append('none')
        sil_k_list.append('none')
        cal_list.append('none')
        cal_k_list.append('none')
        
    if len(data) == 1:
        sil_list.append('one_pore')
        sil_k_list.append('one_pore')
        cal_list.append('one_pore')
        cal_k_list.append('one_pore')
    if len(data) > 1:
        if len(set(c_list)) == 1:
            sil_list.append('one_pore')
            sil_k_list.append('one_pore')
            cal_list.append('one_pore')
            cal_k_list.append('one_pore')            
        if len(set(c_list)) > 1:
            silhouette = metrics.silhouette_score(data, c_list, metric = 'euclidean')        
            sil_list.append(silhouette)
            calinski = metrics.calinski_harabasz_score(data, c_list)
            cal_list.append(calinski)
            
            kmeans = KMeans(n_clusters = len(set(c_list)), random_state = 40)
            sil_k = metrics.silhouette_score(data, kmeans.fit_predict(data))
            sil_k_list.append(sil_k)
            cal_k = metrics.calinski_harabasz_score(data, kmeans.fit_predict(data))
            cal_k_list.append(cal_k)

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

...

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/home/sbml/anaconda3/envs/mayavi/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The defa

In [67]:
b = pd.read_csv('/home/sbml/Desktop/0.solid_electrolyte/feature_extraction_240728/extracted_bare.csv')
b = b.drop(['Unnamed: 0'], axis = 1)
b['silhouette_pore'] = sil_list
b['silhouette_pore_kmeans'] = sil_k_list
b['calinski_pore'] = cal_list
b['calinski_pore_kmeans'] = cal_k_list
b.to_csv('/home/sbml/Desktop/0.solid_electrolyte/feature_extraction_240728/extracted_bare.csv')

In [68]:
b

ncm_ind         volume_raw   volume  \
0          0           [2304.5]   2304.5   
1          1          [13894.5]  13894.5   
2          2           [1068.0]   1068.0   
3          3           [3837.5]   3837.5   
4          4          [26733.5]  26733.5   
..       ...                ...      ...   
495      495            [882.5]    882.5   
496      496            [509.5]    509.5   
497      497           [7214.5]   7214.5   
498      498  [54172.0, 4325.0]  58497.0   
499      499           [3760.5]   3760.5   

                           surface_area_raw  surface_area  \
0                        [751.369619011879]    751.369619   
1                       [2526.353585600853]   2526.353586   
2                      [400.66399443149567]    400.663994   
3                      [1088.6559777259827]   1088.655978   
4                       [4019.016703605652]   4019.016704   
..                                      ...           ...   
495                    [456.50461411476135]    456.504614   
496                    [221.09545290470123]    221.095453   
497                     [1850.184977054596]   1850.184977   
498  [7673.57042324543, 1191.4894571304321]   8865.059880   
499                    [1161.6193999052048]   1161.619400   

                                      dist_from_center  \
0    [[241.00622398602076, 241.00622398602076, 241....   
1    [[203.00246303924493, 203.00246303924493, 203....   
2    [[372.7800960351826, 373.99064159414473, 373.0...   
3    [[946.1469230515945, 944.7645209257172, 943.92...   
4    [[524.4091913763526, 523.442451469118, 522.220...   
..                                                 ...   
495  [[377.0331550407736, 376.14491888100787, 376.3...   
496  [[591.8487982584742, 591.8487982584742, 590.71...   
497  [[846.1784681732336, 844.7674236143342, 844.10...   
498  [[812.8726837580409, 812.8726837580409, 811.93...   
499  [[351.6546601425893, 350.4868043165106, 351.30...   

                                  dist_mean  \
0                       [240.9248646308442]   
1                      [201.81956560596493]   
2                      [372.14773869274313]   
3                       [942.8262352497466]   
4                       [525.0500333105152]   
..                                      ...   
495                     [376.0547642870997]   
496                     [591.0496404703846]   
497                     [841.8342718240234]   
498  [792.7685975331291, 762.1675783140787]   
499                    [351.59691060176044]   

                   frame_per_uniformity_raw  frame_per_uniformity  \
0                         [5.3457560570145]              5.345756   
1                       [6.782632269067978]              6.782632   
2                       [3.796750456930338]              3.796750   
3                       [6.142013587361969]              6.142014   
4                       [6.848908550979194]              6.848909   
..                                      ...                   ...   
495                     [6.733815305525624]              6.733815   
496                     [2.603635188420545]              2.603635   
497                    [7.8258723469278415]              7.825872   
498  [9.145341336603172, 6.027171525416321]             15.172513   
499                     [7.852636209787166]              7.852636   

     contact_area_pore_side  contact_area_mean_pore_side  \
0                  0.000000                     0.000000   
1                466.622762                    27.448398   
2                  9.000000                     9.000000   
3                  6.472136                     2.157379   
4                 71.398977                    11.899829   
..                      ...                          ...   
495                0.000000                     0.000000   
496                0.000000                     0.000000   
497               54.308159                     6.788520   
498              426.717919                    17.06